In [1]:
import numpy as np
import pandas as pd
from re import sub
from time import time
import pickle

from comet_ml import Experiment

from keras.models import Sequential
from keras.layers import Dense, BatchNormalization, Dropout
from keras_tqdm import TQDMNotebookCallback as ktqdm
from keras.utils import normalize
from keras.wrappers.scikit_learn import KerasRegressor
from keras.callbacks import TensorBoard
from keras.optimizers import Adam, SGD
from keras.regularizers import l1, l2
from keras.initializers import RandomUniform, RandomNormal
from keras.layers.advanced_activations import LeakyReLU

from tensorflow.nn import relu, softmax

from sklearn import preprocessing
from sklearn.model_selection import train_test_split, StratifiedKFold, KFold
from sklearn.preprocessing import RobustScaler, MinMaxScaler, StandardScaler, Normalizer
from sklearn.impute import SimpleImputer
from sklearn.datasets import make_regression
from sklearn.metrics import mean_squared_error, r2_score

import scipy.stats as st

import seaborn as sns

import matplotlib.pyplot as plt

Using TensorFlow backend.


In [2]:
experiment = Experiment(api_key="CndJ3YmXyZcxmsV8EccJEuu9C",
                        project_name="Regression_all_features", workspace="paologalligit")

COMET INFO: old comet version (1.0.56) detected. current: 2.0.2 please update your comet lib with command: `pip install --no-cache-dir --upgrade comet_ml`
COMET INFO: Experiment is live on comet.ml https://www.comet.ml/paologalligit/regression-all-features/5e14f3cb502943e3a5ee14d14fcdd203



In [2]:
def print_dict(d):
    print("{:<15} {:<15} {:<10}".format('NeuralNetwork','MEAN','STD'))
    for k, v in d.items():
        print("{:<15} {:<15} {:<10}".format(k, round(v['MEAN'], 4), round(v['STD'], 4)))

In [16]:
df = pd.read_csv('fifa19.csv')

In [17]:
df.drop(columns=['Unnamed: 0', 'ID', 'Photo', 'Flag', 'Club Logo', 'Real Face', 'Preferred Foot',
                 'Body Type', 'Jersey Number', 'Joined', 'Loaned From', 'Contract Valid Until', 
                 'Name', 'Club', 'Nationality', 'Work Rate', 'Position'],inplace=True)

## Obiettivo: predire valore dei giocatori

Pre-processing: convertire value, wage e release clause da string a float

In [18]:
curs=["Release Clause", "Value", "Wage"]

for cur in curs:
    def curr2val(x):
        x = str(x).replace('€', '')
        if 'K' in x: x = float(str(x).replace('K', '')) * 1000
        else: x = float(str(x).replace('M', '')) * 1000000
        return x
    df[cur] = df[cur].apply(curr2val)
    

Individuare eventuali outlier nella colonna value

In [19]:
def detect_outlier(data, threshold = 3):
    outliers=[]
    mean = np.mean(data)
    std = np.std(data)
    
    for y in data:
        score= (y - mean) / std 
        if np.abs(score) > threshold:
            outliers.append(y)
    return outliers

In [20]:
min_out = min(detect_outlier(df['Value'], threshold = 2))

df = df[df['Value'] < min_out] 
df = df[df['Value'] > 0]

Conversione in interi per le altre label

In [21]:
cols=["LS", "ST", "RS", "LW", "LF", "CF", "RF", "RW","LAM", "CAM", "RAM", "LM", "LCM", "CM", "RCM", "RM", "LWB", "LDM","CDM", "RDM", "RWB", "LB", "LCB", "CB", "RCB", "RB"]
for col in cols:
    df[col] = df[col].str[:-2]
    df[col] = df[col].astype(float)

In [22]:
df['Height'] = df['Height'].str.replace("'",'.')
df['Height'] = df['Height'].astype(float)

df['Weight'] = df['Weight'].str[:-3]
df['Weight'] = df['Weight'].astype(float)

Mescolo le righe del dataset

In [23]:
df_flt = df.sample(frac=1)

train_slice = int(len(df_flt) * 0.8)

train = df_flt[:train_slice]
test = df_flt[train_slice:]

In [24]:
y_train = train.loc[:, ['Value']]
X_train = train.drop(columns='Value')

y_test = test.loc[:, ['Value']]
X_test = test.drop(columns='Value')

Sostiuisco eventuali valori nan con la media della colonna

In [25]:
X_train.iloc[:,55:].describe()

LongShots    Aggression  Interceptions   Positioning        Vision  \
count  13893.000000  13893.000000   13893.000000  13893.000000  13893.000000   
mean      46.546102     55.490823      46.236882     49.440294     52.804578   
std       18.914487     17.249470      20.518571     19.207431     13.722032   
min        3.000000     11.000000       3.000000      2.000000     10.000000   
25%       32.000000     43.000000      25.000000     38.000000     43.000000   
50%       51.000000     58.000000      52.000000     55.000000     54.000000   
75%       62.000000     69.000000      64.000000     64.000000     63.000000   
max       89.000000     95.000000      90.000000     87.000000     87.000000   

          Penalties     Composure       Marking  StandingTackle  \
count  13893.000000  13893.000000  13893.000000    13893.000000   
mean      48.113510     58.024113     46.845822       47.318146   
std       15.445934     11.033001     19.684259       21.498153   
min        5.000000      3.000000      3.000000        5.000000   
25%       38.000000     51.000000     30.000000       26.000000   
50%       49.000000     59.000000     52.000000       55.000000   
75%       60.000000     66.000000     63.000000       66.000000   
max       90.000000     88.000000     94.000000       90.000000   

       SlidingTackle      GKDiving    GKHandling     GKKicking  GKPositioning  \
count   13893.000000  13893.000000  13893.000000  13893.000000   13893.000000   
mean       45.348593     16.610883     16.378104     16.215720      16.369611   
std        21.117272     17.595493     16.798956     16.408526      16.910660   
min         3.000000      1.000000      1.000000      1.000000       1.000000   
25%        24.000000      8.000000      8.000000      8.000000       8.000000   
50%        52.000000     11.000000     11.000000     11.000000      11.000000   
75%        64.000000     14.000000     14.000000     14.000000      14.000000   
max        86.000000     88.000000     87.000000     85.000000      90.000000   

         GKReflexes  Release Clause  
count  13893.000000    1.289400e+04  
mean      16.692075    3.039186e+06  
std       17.844000    4.773160e+06  
min        1.000000    1.300000e+04  
25%        8.000000    5.040000e+05  
50%       11.000000    1.100000e+06  
75%       14.000000    2.900000e+06  
max       86.000000    3.040000e+07

In [26]:
imputer = SimpleImputer(missing_values = np.nan, strategy = 'mean')
imputer = imputer.fit(X_train)
X_full = imputer.transform(X_train)

imputer = SimpleImputer(missing_values = np.nan, strategy = 'mean')
imputer = imputer.fit(y_train)
y_full = imputer.transform(y_train)

imputer = SimpleImputer(missing_values = np.nan, strategy = 'mean')
imputer = imputer.fit(X_test)
X_test_full = imputer.transform(X_test)

imputer = SimpleImputer(missing_values = np.nan, strategy = 'mean')
imputer = imputer.fit(y_test)
y_test_full = imputer.transform(y_test)

Scalo i valori, sia per i caratteri che per il target

In [27]:
# scaler = RobustScaler()
# scaler = scaler.fit(X_train)
# X_train = scaler.transform(X_train)

# X_train_scaled = preprocessing.scale(X_train)
scaler = StandardScaler().fit(X_full)
X_scaled = scaler.transform(X_full)

scaler_train = StandardScaler().fit(y_full)
y_scaled = scaler_train.transform(y_full) 
# X_train_scaled, X_test_scaled

scaler = StandardScaler().fit(X_test_full)
X_test_scaled = scaler.transform(X_test_full)

scaler_test = StandardScaler().fit(y_test_full)
y_test_scaled = scaler_test.transform(y_test_full) 

np.isnan(y_test_full).any()

False

In [28]:
data = {
    'X_scaled': X_scaled,
    'y_scaled': y_scaled,
    'X_test_scaled': X_test_scaled,
    'y_test_scaled': y_test_scaled,
    'y_test_full': y_test_full,
}

with open('dataset_full_labels', 'wb') as f:
    pickle.dump(data, f)

In [17]:
def coeff_determination(y_test, y_pred):
    from keras import backend as K
    SS_res =  K.sum(K.square( y_test-y_pred ))
    SS_tot = K.sum(K.square( y_test - K.mean(y_test) ) )
    return ( 1 - SS_res/(SS_tot + K.epsilon()))

In [18]:
ts_board = TensorBoard(log_dir='value_predictions_v3/{}'.format('kfold_' + str(time())))

In [19]:
def mean_abs_error(prediction, target):
    res = 0
    tot = 0
    for i in range(len(target)):
        if target[i][0] != 0 and not np.isnan(prediction[i][0]):
            res += abs(prediction[i][0] - target[i][0])
            tot += 1
    return round(res / tot, 2)

# Cross-validation
### K-Fold

In [20]:
# kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=0)
outer_kfold = KFold(n_splits=3, random_state=42, shuffle=False)
inner_kfold = KFold(n_splits=5, random_state=19, shuffle=False )

In [21]:
def build_nn(input_layer, neurons):
    model = Sequential()

    model.add(Dense(neurons, input_dim = input_layer, activation='relu'))

    model.add(Dense(1, activation = 'linear'))
    
    return model

In [22]:
opt = Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)

Instructions for updating:
Colocations handled automatically by placer.


In [23]:
total_results = []

for fold, (train_index_outer, test_index_outer) in enumerate(outer_kfold.split(X_scaled)):
    
    X_train_outer, X_test_outer = X_scaled[train_index_outer], X_scaled[test_index_outer]
    y_train_outer, y_test_outer = y_scaled[train_index_outer], y_scaled[test_index_outer]
    
    inner_mean_scores = []

    neurons = range(10, 210, 10)
    
    for neuron in neurons:
        
        inner_scores = []
        
        for train_index_inner, test_index_inner in inner_kfold.split(X_train_outer):
            X_train_inner, X_test_inner = X_train_outer[train_index_inner], X_train_outer[test_index_inner]
            y_train_inner, y_test_inner = y_train_outer[train_index_inner], y_train_outer[test_index_inner]

            nn = build_nn(X_train_inner.shape[1], neuron)
            nn.compile(optimizer=opt, loss='mean_absolute_error', metrics=[coeff_determination])
            nn.fit(X_train_inner, y_train_inner, batch_size=125, epochs=100, shuffle=True, verbose=1)

            res = nn.predict(X_test_inner)
            loss, acc = nn.evaluate(X_train_inner, y_train_inner, verbose=1)
            
            reversed_res = scaler_train.inverse_transform(res)
            reversed_label = scaler_train.inverse_transform(y_test_inner)
            inner_scores.append(
                {'ACC': acc * 100, 'MAE': mean_abs_error(reversed_res, reversed_label), 'MAX': max(reversed_label), 'MEAN': round(np.mean(reversed_label), 4)}
            )
            
            print("loss: %.4f, acc: %.4f%%" % (loss, acc*100))
        
        inner_mean_scores.append({'n_{}'.format(neuron): inner_scores})
    total_results.append({'fold_{}'.format(fold): inner_mean_scores})

Instructions for updating:
Use tf.cast instead.
Epoch 1/100
7428/7428 [==============================] - 1s 94us/step - loss: 0.6179 - coeff_determination: 0.1384
Epoch 2/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.3508 - coeff_determination: 0.7359
Epoch 3/100
7428/7428 [==============================] - 0s 10us/step - loss: 0.2549 - coeff_determination: 0.8553
Epoch 4/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.2095 - coeff_determination: 0.8939
Epoch 5/100
7428/7428 [==============================] - 0s 10us/step - loss: 0.1840 - coeff_determination: 0.9102
Epoch 6/100
7428/7428 [==============================] - 0s 10us/step - loss: 0.1677 - coeff_determination: 0.9191
Epoch 7/100
7428/7428 [==============================] - 0s 10us/step - loss: 0.1547 - coeff_determination: 0.9243
Epoch 8/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.1445 - coeff_determination: 0.9315
Epoch 9/100
7428/7428 [============

7428/7428 [==============================] - 0s 9us/step - loss: 0.0724 - coeff_determination: 0.9627
Epoch 40/100
7428/7428 [==============================] - 0s 8us/step - loss: 0.0721 - coeff_determination: 0.9621
Epoch 41/100
7428/7428 [==============================] - 0s 8us/step - loss: 0.0716 - coeff_determination: 0.9636
Epoch 42/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0709 - coeff_determination: 0.9643
Epoch 43/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0711 - coeff_determination: 0.9641
Epoch 44/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0711 - coeff_determination: 0.9654
Epoch 45/100
7428/7428 [==============================] - 0s 8us/step - loss: 0.0701 - coeff_determination: 0.9660
Epoch 46/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0690 - coeff_determination: 0.9657
Epoch 47/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0692 - coeff_

7428/7428 [==============================] - 0s 9us/step - loss: 0.0751 - coeff_determination: 0.9620
Epoch 81/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0743 - coeff_determination: 0.9624
Epoch 82/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0739 - coeff_determination: 0.9631
Epoch 83/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0753 - coeff_determination: 0.9624
Epoch 84/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0739 - coeff_determination: 0.9614
Epoch 85/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0735 - coeff_determination: 0.9632
Epoch 86/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0735 - coeff_determination: 0.9630
Epoch 87/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0749 - coeff_determination: 0.9622
Epoch 88/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0733 - coeff_

7428/7428 [==============================] - 0s 9us/step - loss: 0.0904 - coeff_determination: 0.9535
Epoch 21/100
7428/7428 [==============================] - 0s 8us/step - loss: 0.0905 - coeff_determination: 0.9539
Epoch 22/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0887 - coeff_determination: 0.9545
Epoch 23/100
7428/7428 [==============================] - 0s 10us/step - loss: 0.0890 - coeff_determination: 0.9567
Epoch 24/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0886 - coeff_determination: 0.9563
Epoch 25/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0883 - coeff_determination: 0.9542
Epoch 26/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0869 - coeff_determination: 0.9559
Epoch 27/100
7428/7428 [==============================] - ETA: 0s - loss: 0.0873 - coeff_determination: 0.952 - 0s 9us/step - loss: 0.0872 - coeff_determination: 0.9553
Epoch 28/100
7428/7428 [==============

7428/7428 [==============================] - 0s 10us/step - loss: 0.0756 - coeff_determination: 0.9621
Epoch 61/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0756 - coeff_determination: 0.9614
Epoch 62/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0755 - coeff_determination: 0.9603
Epoch 63/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0749 - coeff_determination: 0.9617
Epoch 64/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0747 - coeff_determination: 0.9620
Epoch 65/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0743 - coeff_determination: 0.9620
Epoch 66/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0746 - coeff_determination: 0.9629
Epoch 67/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0740 - coeff_determination: 0.9636
Epoch 68/100
7428/7428 [==============================] - 0s 9us/step - loss: 0.0738 - coeff

...

Epoch 65/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0478 - coeff_determination: 0.9889
Epoch 66/100
7429/7429 [==============================] - 0s 64us/step - loss: 0.0469 - coeff_determination: 0.9893
Epoch 67/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0471 - coeff_determination: 0.9895
Epoch 68/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0468 - coeff_determination: 0.9896
Epoch 69/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0471 - coeff_determination: 0.9891
Epoch 70/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0469 - coeff_determination: 0.9902
Epoch 71/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0440 - coeff_determination: 0.9909
Epoch 72/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0451 - coeff_determination: 0.9904
Epoch 73/100
7429/7429 [==============================] - 0s 65us/step -

7429/7429 [==============================] - 0s 65us/step - loss: 0.1016 - coeff_determination: 0.9496
Epoch 5/100
7429/7429 [==============================] - 0s 64us/step - loss: 0.0968 - coeff_determination: 0.9526
Epoch 6/100
7429/7429 [==============================] - 0s 67us/step - loss: 0.0986 - coeff_determination: 0.9538
Epoch 7/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0882 - coeff_determination: 0.9570
Epoch 8/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0877 - coeff_determination: 0.9578
Epoch 9/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0893 - coeff_determination: 0.9579
Epoch 10/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0827 - coeff_determination: 0.9614
Epoch 11/100
7429/7429 [==============================] - 0s 60us/step - loss: 0.0786 - coeff_determination: 0.9615
Epoch 12/100
7429/7429 [==============================] - 1s 70us/step - loss: 0.0779 - co

7429/7429 [==============================] - 1s 68us/step - loss: 0.0562 - coeff_determination: 0.9864
Epoch 45/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0525 - coeff_determination: 0.9874
Epoch 46/100
7429/7429 [==============================] - 1s 68us/step - loss: 0.0526 - coeff_determination: 0.9876
Epoch 47/100
7429/7429 [==============================] - 0s 67us/step - loss: 0.0514 - coeff_determination: 0.9877
Epoch 48/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0519 - coeff_determination: 0.9879
Epoch 49/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0522 - coeff_determination: 0.9881
Epoch 50/100
7429/7429 [==============================] - 1s 68us/step - loss: 0.0527 - coeff_determination: 0.9880
Epoch 51/100
7429/7429 [==============================] - 1s 67us/step - loss: 0.0516 - coeff_determination: 0.9879
Epoch 52/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0482

7429/7429 [==============================] - 0s 66us/step - loss: 0.0754 - coeff_determination: 0.9645
Epoch 15/100
7429/7429 [==============================] - 0s 67us/step - loss: 0.0763 - coeff_determination: 0.9651
Epoch 16/100
7429/7429 [==============================] - 1s 74us/step - loss: 0.0740 - coeff_determination: 0.9660
Epoch 17/100
7429/7429 [==============================] - 1s 77us/step - loss: 0.0723 - coeff_determination: 0.9661
Epoch 18/100
7429/7429 [==============================] - 1s 78us/step - loss: 0.0712 - coeff_determination: 0.9676
Epoch 19/100
7429/7429 [==============================] - 1s 86us/step - loss: 0.0708 - coeff_determination: 0.9686
Epoch 20/100
7429/7429 [==============================] - 1s 79us/step - loss: 0.0694 - coeff_determination: 0.9687
Epoch 21/100
7429/7429 [==============================] - 1s 72us/step - loss: 0.0709 - coeff_determination: 0.9683
Epoch 22/100
7429/7429 [==============================] - 1s 70us/step - loss: 0.0688

7429/7429 [==============================] - 0s 66us/step - loss: 0.0527 - coeff_determination: 0.9822
Epoch 55/100
7429/7429 [==============================] - 0s 65us/step - loss: 0.0519 - coeff_determination: 0.9822
Epoch 56/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0502 - coeff_determination: 0.9842
Epoch 57/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0507 - coeff_determination: 0.9843
Epoch 58/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0501 - coeff_determination: 0.9840
Epoch 59/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0512 - coeff_determination: 0.9838
Epoch 60/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0510 - coeff_determination: 0.9846
Epoch 61/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0506 - coeff_determination: 0.9850
Epoch 62/100
7429/7429 [==============================] - 0s 66us/step - loss: 0.0521

In [24]:
total_results

[{'fold_0': [{'n_10': [{'ACC': 96.78114938299439,
      'MAE': 170314.27,
      'MAX': array([13500000.]),
      'MEAN': 1610503.5003},
     {'ACC': 97.6276373311147,
      'MAE': 161927.85,
      'MAX': array([13500000.]),
      'MEAN': 1750923.5326},
     {'ACC': 96.69973069644449,
      'MAE': 172182.07,
      'MAX': array([13500000.]),
      'MEAN': 1683581.0447},
     {'ACC': 96.75527197029493,
      'MAE': 182953.94,
      'MAX': array([13500000.]),
      'MEAN': 1746222.4017},
     {'ACC': 96.9839078287444,
      'MAE': 187913.21,
      'MAX': array([13000000.]),
      'MEAN': 1733357.566}]},
   {'n_20': [{'ACC': 96.87470381595014,
      'MAE': 174438.24,
      'MAX': array([13500000.]),
      'MEAN': 1610503.5003},
     {'ACC': 98.23663135530106,
      'MAE': 154118.06,
      'MAX': array([13500000.]),
      'MEAN': 1750923.5326},
     {'ACC': 97.57481269060956,
      'MAE': 158443.22,
      'MAX': array([13500000.]),
      'MEAN': 1683581.0447},
     {'ACC': 97.73305047245262,

In [26]:
nn = build_nn(X_scaled.shape[1], 170)
nn.compile(optimizer=opt, loss='mean_absolute_error', metrics=[coeff_determination])
nn.fit(X_scaled, y_scaled, batch_size=125, epochs=100, shuffle=True, verbose=1)

res = nn.predict(X_test_scaled)

scaler_test = StandardScaler().fit(y_test.values)
res = scaler_test.inverse_transform(res)

mean_abs_error(res, y_test.values), max(y_test.values), round(np.mean(y_test.values), 2), round(r2_score(y_test.values, res), 4)

Epoch 1/100
13928/13928 [==============================] - 3s 222us/step - loss: 0.2029 - coeff_determination: 0.8741
Epoch 2/100
13928/13928 [==============================] - 1s 67us/step - loss: 0.1125 - coeff_determination: 0.9439
Epoch 3/100
13928/13928 [==============================] - 1s 68us/step - loss: 0.1000 - coeff_determination: 0.9507
Epoch 4/100
13928/13928 [==============================] - 1s 68us/step - loss: 0.0927 - coeff_determination: 0.9546
Epoch 5/100
13928/13928 [==============================] - 1s 72us/step - loss: 0.0892 - coeff_determination: 0.9564
Epoch 6/100
13928/13928 [==============================] - 1s 73us/step - loss: 0.0859 - coeff_determination: 0.9592
Epoch 7/100
13928/13928 [==============================] - 1s 74us/step - loss: 0.0818 - coeff_determination: 0.9616
Epoch 8/100
13928/13928 [==============================] - 1s 75us/step - loss: 0.0784 - coeff_determination: 0.9630
Epoch 9/100
13928/13928 [==============================] - 1s 7

(124689.15, array([13500000.]), 1604094.17, 0.9921)